## <font color='blue'>SME0104 - Cálculo Numérico</font>

### Primeiro Trabalho em Grupo 
#### Comparação de Métodos na Solução do Laplaciano em Grafos para propagação de informação

**Luis Gustavo Nonato**

------

- Felipe Cadavez Oliveira
  - 11208558
- Giovanni Shibaki Camargo
  - 11796444
- João Victor Sene Araujo
  - 11796382
- Lucas Keiti Anbo Mihara
  - 11796472

### Github do projeto
- https://github.com/giovanni-shibaki/SME104_Laplacian

Considere os arquivos `manh.el` e `manh.xy` que fornecem as arestas e as coordenadas dos vértices do grafo de ruas da ilha de Manhattan, NY (arquivos disponíveis para download no Google Drive).

O grafo de ruas possui diversas componentes conexas, considerando somente a maior componente conexa, você deve realizar as seguintes tarefas:
1. Selecione alguns vértices do grafo $v_{i_1},v_{i_2},\ldots,v_{i_k},\, k<<n$ ($n$ é o número de vértices na maior componente do grafo e $k$ é um número bem menor que $n$, $k=10$ por exemplo) e atribua valores distindos $c_{i_1},c_{i_2},\ldots,c_{i_k}$ a cada um dos vértices selecionados (por exemplo valores no intervalo (0,10]);
2. Construa a matriz Laplaciana $L$ do grafo de ruas;
3. Construa a matriz de penalidades $P$, sendo $P$ é uma matriz diagonal onde a entrada $P_{jj}=\alpha$ se $j$ corresponde ao índice de algum dos vértices escolhidos no item 1 acima ($\alpha=1.0e7$ por exemplo), sendo $P_{ii}=0$ caso contrário.
4. Construa um vetor $b$ da seguinte forma:
$$
b_{j} = \left\{\begin{matrix} c_{i_s} & \mbox{ se } j = i_s \\ 0 & \mbox{ caso contrário}\end{matrix}\right.
$$
5. Compare o tempo de solução do sistema
$$
(L+P)x = Pb
$$
para os métodos:
    - Decomposição LU
    - Cholesky
    - Jacobi e Gaus-Seidel
    - Gradientes Conjugados
    
6. Refaça as tarefas com representação por matriz esparsa e matrizes cheias, comparando os resultados.

In [76]:
# Bibliotecas Usadas

# Instalações necessárias para a biblioteca sksparse.cholmod (funciona no google collab)
!apt-get install python-scipy libsuitesparse-dev
!pip install scikit-sparse

import numpy as np
import networkx as nx
import random
import time
import scipy
import scipy.linalg
import scipy.sparse.linalg
import matplotlib.pyplot as plt

# Biblioteca necessária para o método de Cholesky para matrizes esparsas
from sksparse.cholmod import cholesky

In [77]:
# Leitura dos arquivos manh.el e manh.xy
# E criação do grafo

# Leitura do arquivo manh.el para a criação da matriz de adjacencia
file1 = open('manh.el', 'r')
Lines = file1.readlines()

# Criação do grafo direcionado
Graph = nx.Graph();

max = 0
for line in Lines:
    values = line.split()
    x, y = values[0], values[1]
    if(int(x) > max):
        max = int(x)
    if(int(y) > max):
        max = int(y)

numNodes = max + 1
print("O grafo possui ",numNodes,"vértices")

for i in range(numNodes):
    Graph.add_node(i)

for line in Lines:
    values = line.split()
    x, y = values[0], values[1]
    Graph.add_edge(int(x), int(y))
    Graph.add_edge(int(y), int(x))

#Graph2 = Graph.subgraph(range(50))
# Plotando o grafo correspondente
#plt.figure(1, figsize=(200,200))
#nx.draw(Graph2, pos=nx.circular_layout(Graph2), with_labels=True)

O grafo possui  8837 vértices


In [78]:
stronglyConnectedComponents = [Graph.subgraph(c).copy() for c in nx.connected_components(Graph)]

for item in stronglyConnectedComponents:
    print(item)
    print(nx.is_connected(item))

maximum = 0
for item in stronglyConnectedComponents:
    if item.number_of_nodes() > maximum:
        Graph2 = item
        maximum = item.number_of_nodes()

print("\n",Graph2)

Graph with 8708 nodes and 13556 edges
True
Graph with 123 nodes and 154 edges
True
Graph with 2 nodes and 1 edges
True
Graph with 2 nodes and 1 edges
True
Graph with 2 nodes and 1 edges
True

 Graph with 8708 nodes and 13556 edges


## Matriz de Laplace a partir matriz de Adjacencia e a matriz diagonal com os graus de cada vértice

In [79]:
# Matriz de laplace

laplaceMatrix = nx.adjacency_matrix(Graph2)

# Matriz de adjacência
print("Matriz de adjacencia")
MA = nx.to_numpy_array(Graph2)
print(MA)

print()

# Matriz diagonal com os graus de cada vértice
MD = np.diag(np.sum(MA,axis=1))

print()
print("Matriz diagonal com os graus dos vértices")
print(MD)
print()

Matriz de adjacencia
[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]


Matriz diagonal com os graus dos vértices
[[3. 0. 0. ... 0. 0. 0.]
 [0. 2. 0. ... 0. 0. 0.]
 [0. 0. 2. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 3. 0. 0.]
 [0. 0. 0. ... 0. 2. 0.]
 [0. 0. 0. ... 0. 0. 1.]]



In [80]:
# Matriz de Laplace calculada
LA = MD - MA
print("Matriz de Laplace calculada a partir das matrizes diagonal de grau e matriz de adjacencia:")
print(LA)
print()

count = 0
for item in LA:
    for item2 in item:
        if(item2 == -1):
            count += 1
print(count)

Matriz de Laplace calculada a partir das matrizes diagonal de grau e matriz de adjacencia:
[[3. 0. 0. ... 0. 0. 0.]
 [0. 2. 0. ... 0. 0. 0.]
 [0. 0. 2. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 3. 0. 0.]
 [0. 0. 0. ... 0. 2. 0.]
 [0. 0. 0. ... 0. 0. 1.]]

27112


## Matriz de penalidades

In [68]:
# escolhendo eleatóriamente os pontos com valores dados
pMatrix = np.zeros([8708, 8708])

b = np.zeros([8708])

# Foram escolhidos 20 valores dados
for i in range(20):
    lineColumn = random.randint(0, 8707)
    pMatrix[lineColumn, lineColumn] = 1e7
    value = random.random() * 10
    b[lineColumn] = value
    print(lineColumn, "= ", value)


# Pontos dados referentes à primeira imagem de Manhattan
# 4196 =  0.49507385388131153
# 7142 =  0.010562482363345449
# 7321 =  9.42829613325248
# 6905 =  3.5808324130075553
# 4477 =  9.214190663713008
# 1048 =  2.85198641824302
# 127 =  1.6862495751856599
# 6145 =  8.985509425678032
# 3069 =  3.948287855808167
# 2211 =  6.069468516828481
# 2559 =  9.21744643790199
# 5283 =  2.7716613927811795
# 2927 =  3.5784923862653706
# 7084 =  8.683992693841603
# 7659 =  4.060631299772125
# 855 =  4.138174172298842
# 1879 =  8.695047355835495
# 2303 =  5.539705989152306
# 2023 =  2.1051932396952653
# 8375 =  2.559298205987516

# Pontos dados referentes à segunda imagem de Manhattan
# 756 =  6.541168874240721
# 6990 =  3.366867088085912
# 2653 =  4.30155257673036
# 7797 =  3.3043186413215144
# 560 =  4.330283368268683
# 1920 =  5.763201083497931
# 6242 =  0.7760779430696285
# 8137 =  7.178654354623628
# 4440 =  3.863078280676906
# 2210 =  2.445330455675955
# 6637 =  2.8186637489990005
# 2340 =  4.339094688091998
# 1958 =  5.415659641899789
# 4659 =  2.805980458208708
# 2103 =  0.18275484792176444
# 8414 =  0.44266063113857723
# 4336 =  0.5308261952446625
# 3972 =  0.8772906985651274
# 1136 =  5.505516857300506
# 302 =  9.027767591576463

# Pontos dados referentes à terceira imagem de Manhattan
# 7581 =  9.316358953958444
# 6381 =  6.381718958195433
# 3810 =  9.65449930113022
# 1097 =  1.770048091684332
# 6550 =  0.04751878129765186
# 107 =  3.274005877352093
# 1556 =  1.5204526870244206
# 781 =  8.575150164674774
# 5469 =  6.145259140952461
# 2986 =  8.433038376502981
# 4301 =  7.127242666384658
# 7810 =  9.756417525540984
# 2040 =  3.8103474946791493
# 433 =  9.6429318489586
# 5937 =  4.220678374254928
# 1972 =  4.067237065968632
# 5533 =  1.4068790218751215
# 5234 =  7.131491452411083
# 826 =  3.327344198932458
# 6895 =  0.2902214285910898

# Pontos dados referentes à quarta imagem de Manhattan
# 6021 =  1.0530538640276788
# 135 =  1.148194882940743
# 6346 =  6.693884059714936
# 7524 =  5.062211029679833
# 8697 =  6.086766456762306
# 1720 =  3.6416688669410524
# 2020 =  1.7852039731457003
# 831 =  1.6339262931346499
# 3782 =  9.148630711503111
# 6173 =  4.8771668247214475
# 1234 =  4.74526542503345
# 1005 =  1.1700458068451824
# 401 =  1.7761897760165501
# 2715 =  3.1921883011959573
# 8169 =  7.592628507227409
# 8111 =  6.875467593482478
# 4602 =  6.700774991779813
# 5781 =  5.403031387752202
# 394 =  0.916425542346998
# 8081 =  3.84960439140674

6021 =  1.0530538640276788
135 =  1.148194882940743
6346 =  6.693884059714936
7524 =  5.062211029679833
8697 =  6.086766456762306
1720 =  3.6416688669410524
2020 =  1.7852039731457003
831 =  1.6339262931346499
3782 =  9.148630711503111
6173 =  4.8771668247214475
1234 =  4.74526542503345
1005 =  1.1700458068451824
401 =  1.7761897760165501
2715 =  3.1921883011959573
8169 =  7.592628507227409
8111 =  6.875467593482478
4602 =  6.700774991779813
5781 =  5.403031387752202
394 =  0.916425542346998
8081 =  3.84960439140674


## Comparação do tempo de resolução do sistema

### Decomposição LU

In [ ]:
# Decomposição LU
start_time = time.time()

A = (LA + pMatrix)
B = b @ pMatrix

lu, piv = scipy.linalg.lu_factor(A)
x = scipy.linalg.lu_solve((lu, piv), B)
print(x)

print("Solucionar o sistema por meio da decomposição LU tomou: ",time.time() - start_time,"segundos")
print("É solução do sistema com tolerância 1e-7? \n",np.allclose(A @ x - B, np.zeros((8708,)), rtol=1e-7, atol=1e-7))

[5.97225991 4.43268357 5.11619691 ... 6.23325918 4.93107003 5.70649753]
Solucionar o sistema por meio da decomposição LU tomou:  2.9992997646331787 segundos
É solução do sistema com tolerância 1e-7? 
 True


### Cholesky

In [ ]:
# Cholesky
start_time = time.time()

A = (LA + pMatrix)
B = b @ pMatrix

cho, low = scipy.linalg.cho_factor(A)
x = scipy.linalg.cho_solve((cho, low), B)
print(x)

print("Solucionar o sistema por meio do método de Cholesky tomou: ",time.time() - start_time,"segundos")
print("É solução do sistema com tolerância 1e-7? \n",np.allclose(A @ x - B, np.zeros((8708,)), rtol=1e-7, atol=1e-7))

[6.35022685 6.72771885 7.34260261 ... 6.27351216 5.68063851 5.91187028]
Solucionar o sistema por meio do método de Cholesky tomou:  9.455561399459839 segundos
É solução do sistema com tolerância 1e-7? 
 True


### Gauss-Jacobi

In [ ]:
# Gauss-Jacobi
A = (LA + pMatrix)
B = b @ pMatrix

start_time = time.time()
def gauss_jacobi(A, b, x0, tol):
    n = A.shape[0]
    D = np.diag(np.diag(A))
    C = np.eye(n) - scipy.linalg.solve(D, A)
    g = scipy.linalg.solve(D, b)
    kmax = 100000
    k = 0
    while scipy.linalg.norm((b - np.dot(A, x0))) > tol: #and k < kmax:
        k = k + 1
        x0 = np.dot(C, x0) + g
    if k > kmax:
        print("ERRO: Demorou mais que 100000 passos para convergir O.o")
        #exit()
    x = x0
    return x, k

x0 = np.zeros([8708])
x, k = gauss_jacobi(A, B, x0, 1e-7)
print(x)

print("Solucionar o sistema por meio do método de Gauss-Jacobi tomou: ",time.time() - start_time,"segundos")
print("É solução do sistema com tolerância 1e-7? \n",np.allclose(A @ x - B, np.zeros((8708,)), rtol=1e-7, atol=1e-7))

[5.97225731 4.43268344 5.11619673 ... 6.23325901 4.9310694  5.70649434]
Solucionar o sistema por meio do método de Gauss-Jacobi tomou:  2806.319766998291 segundos
É solução do sistema com tolerância 1e-7? 
 True


### Gauss-Seidel

In [ ]:
# Gauss-Seidel
A = (LA + pMatrix)
B = b @ pMatrix

start_time = time.time()
def gauss_seidel(A, b, x0, tol):
    n = A.shape[0]
    L = np.tril(A)
    R = np.triu(A, 1)
    C = -scipy.linalg.solve(L, R)
    g = scipy.linalg.solve(L, b)
    kmax = 10000
    k = 0
    while scipy.linalg.norm((b - np.dot(A, x0))) > tol: #and k < kmax:
        k = k + 1
        x0 = np.dot(C, x0) + g
    if k >= kmax:
        print("Demorou mais que 100000 passos para convergir O.o")
        #exit()
    x = x0
    return x, k

x0 = np.zeros([8708])
x, k = gauss_seidel(A, B, x0, 1e-7)
print(x)

print("Solucionar o sistema por meio do método de Gauss-Seidel tomou: ",time.time() - start_time,"segundos")
print("É solução do sistema com tolerância 1e-7? \n",np.allclose(A @ x - B, np.zeros((8708,)), rtol=1e-7, atol=1e-7))

Demorou mais que 100000 passos para convergir O.o
[5.97225779 4.43268346 5.11619676 ... 6.23325904 4.93106952 5.70649494]
Solucionar o sistema por meio do método de Gauss-Seidel tomou:  1751.0766441822052 segundos
É solução do sistema com tolerância 1e-7? 
 True


### Gradientes Conjugados

In [ ]:
# Gradientes Conjugados
A = (LA + pMatrix)
B = b @ pMatrix

start_time = time.time()

x, info = scipy.sparse.linalg.cg(A, B, tol=1e-15, maxiter=1000000)
if(info == 0):
    print("O método converge com a solução: ")
    print(x)
else:
    print("O método não converge!")

print("Solucionar o sistema por meio do método de Gradientes Conjugados tomou: ",time.time() - start_time,"segundos")
print("É solução do sistema com tolerância 1e-7? \n",np.allclose(A @ x - B, np.zeros((8708,)), rtol=1e-7, atol=1e-7))

O método converge com a solução: 
[6.50097088 2.98387991 6.15642416 ... 3.81346365 6.26226842 6.79201446]
Solucionar o sistema por meio do método de Gradientes Conjugados tomou:  21.03818988800049 segundos
É solução do sistema com tolerância 1e-7? 
 True


## Representação por matriz esparsa

In [69]:
A = (LA + pMatrix)
B = b @ pMatrix

# Matriz esparsa de A
S = scipy.sparse.csc_matrix(A)

print("Tempo de execução do método solve para matriz esparsa: ")
start_time = time.time()
print(scipy.sparse.linalg.spsolve(S,B))
print("1: ",time.time() - start_time,"segundos")


print("\nTempo de execução do método solve para matriz cheia: ")
start_time = time.time()
print(scipy.linalg.solve(A,B))
print("2: ",time.time() - start_time,"segundos")

Tempo de execução do método solve para matriz esparsa: 
[4.44431787 3.59237952 4.12763834 ... 4.68405992 5.61035138 4.09557523]
1:  0.015791654586791992 segundos

Tempo de execução do método solve para matriz cheia: 
[4.44431787 3.59237952 4.12763834 ... 4.68405992 5.61035138 4.09557523]
2:  5.350545644760132 segundos


### Decomposição LU

In [ ]:
# Decomposição LU
start_time = time.time()

lu = scipy.sparse.linalg.splu(S)
x = lu.solve(B)
print(x)

print("Solucionar o sistema por meio da decomposição LU em matriz esparsa tomou: ",time.time() - start_time,"segundos")
print("\nÉ solução do sistema com tolerância 1e-7? \n",np.allclose(A @ x - B, np.zeros((8708,)), rtol=1e-7, atol=1e-7))

[6.35022685 6.72771885 7.34260261 ... 6.27351216 5.68063851 5.91187028]
Solucionar o sistema por meio da decomposição LU tomou:  0.03779411315917969 segundos

É solução do sistema com tolerância 1e-7? 
 True


### Cholesky

In [ ]:
# Cholesky

start_time = time.time()
factor = cholesky(S)
x = factor(B)

print(x)

print("Solucionar o sistema por meio do método de Cholesky em matriz esparsa tomou: ",time.time() - start_time,"segundos")
print("\nÉ solução do sistema com tolerância 1e-7? \n",np.allclose(A @ x - B, np.zeros((8708,)), rtol=1e-7, atol=1e-7))

[6.35022685 6.72771885 7.34260261 ... 6.27351216 5.68063851 5.91187028]
Solucionar o sistema por meio do método de Cholesky tomou:  0.019010066986083984 segundos

É solução do sistema com tolerância 1e-7? 
 True


### Gauss-Jacobi

In [ ]:
# Gauss-Jacobi
start_time = time.time()
def sparse_gauss_jacobi(A, b, tol):
    n = A.shape[0]
    x0 = np.zeros([n])

    D = A.diagonal()
    D = scipy.sparse.diags(1/D, shape=(n,n), format = 'csr')
    kmax = 100000
    k = 0
    while np.linalg.norm((b - A.dot(x0))) > tol: #and k < kmax:
        k = k + 1
        x0 = x0 + D.dot((b - A.dot(x0)))
    if k > kmax:
        print("Demorou mais que 100000 passos para convergir O.o")
    x = x0
    return x, k

S = scipy.sparse.csr_matrix(A)
x, k = sparse_gauss_jacobi(S, B, 1e-7)
print(x)

print("Solucionar o sistema por meio do método de Gauss-Jacobi em matriz esparsa tomou: ",time.time() - start_time,"segundos")
print("\nÉ solução do sistema com tolerância 1e-7? \n",np.allclose(A @ x - B, np.zeros((8708,)), rtol=1e-7, atol=1e-7))

[6.35022624 6.72771879 7.34260244 ... 6.27351214 5.68063688 5.91186977]
Solucionar o sistema por meio do método de Gauss-Jacobi em matriz esparsa tomou:  14.05868935585022 segundos

É solução do sistema com tolerância 1e-7? 
 True


### Gauss-Seidel

In [ ]:
# Gauss-Seidel
start_time = time.time()
def gauss_seidel(A, b, tol):
    n = A.shape[0]
    x0 = np.zeros([n])

    L = scipy.sparse.tril(A)
    R = scipy.sparse.triu(A, 1)
    C = -scipy.sparse.linalg.spsolve(L, R)
    g = scipy.sparse.linalg.spsolve(L, b)
    kmax = 10000
    k = 0
    while scipy.linalg.norm((b - A.dot(x0))) > tol: #and k < kmax:
        k = k + 1
        x0 = C.dot(x0) + g
    if k >= kmax:
        print("Demorou mais que 100000 passos para convergir O.o")
    x = x0
    return x, k

x, k = gauss_seidel(S, B, 1e-7)
print(x)

print("Solucionar o sistema por meio do método de Gauss-Seidel em matriz esparsa tomou: ",time.time() - start_time,"segundos")
print("\nÉ solução do sistema com tolerância 1e-7? \n",np.allclose(A @ x - B, np.zeros((8708,)), rtol=1e-7, atol=1e-7))

/usr/local/lib/python3.7/dist-packages/scipy/sparse/linalg/dsolve/linsolve.py:138: SparseEfficiencyWarning: spsolve requires A be CSC or CSR matrix format
  SparseEfficiencyWarning)
/usr/local/lib/python3.7/dist-packages/scipy/sparse/linalg/dsolve/linsolve.py:208: SparseEfficiencyWarning: spsolve is more efficient when sparse b is in the CSC matrix format
  'is in the CSC matrix format', SparseEfficiencyWarning)
/usr/local/lib/python3.7/dist-packages/scipy/sparse/linalg/dsolve/linsolve.py:138: SparseEfficiencyWarning: spsolve requires A be CSC or CSR matrix format
  SparseEfficiencyWarning)


Demorou mais que 100000 passos para convergir O.o
[6.35022638 6.7277188  7.34260248 ... 6.27351214 5.68063725 5.91186989]
Solucionar o sistema por meio do método de Gauss-Seidel em matriz esparsa tomou:  20.303433418273926 segundos

É solução do sistema com tolerância 1e-7? 
 True


 ### Gradientes Conjugados

In [ ]:
# Gradientes Conjugados
B = b @ pMatrix

start_time = time.time()

x, info = scipy.sparse.linalg.cg(S, B, tol=1e-15, maxiter=1000000)
if(info == 0):
    print("O método converge com a solução: ")
    print(x)
else:
    print("O método não converge!")

print("Solucionar o sistema por meio do método de Gradientes Conjugados em matriz esparsa tomou: ",time.time() - start_time,"segundos")
print("\nÉ solução do sistema com tolerância 1e-7? \n",np.allclose(A @ x - B, np.zeros((8708,)), rtol=1e-7, atol=1e-7))

O método converge com a solução: 
[5.97225995 4.43268359 5.11619691 ... 6.23325915 4.93106999 5.70649753]
Solucionar o sistema por meio do método de Gradientes Conjugados tomou:  0.12363409996032715 segundos
É solução do sistema com tolerância 1e-7? 
 True


## Heatmap das ruas de Manhattan

In [70]:
# Solução do sistema (utilizando matriz esparsa para maior eficiência)
x = scipy.sparse.linalg.spsolve(S,B)
print(x)

print(Graph2)
nodeList = list(Graph2)

nodeXList = []
nodeYList = []

# Leitura do arquivo manh.XY para as coordenadas dos pontos
file2 = open('manh.xy', 'r')
Lines2 = file2.readlines()

count = 0
for line in Lines2:
    values = line.split()
    y, z = values[0], values[1]
    if count in nodeList:
        nodeXList.append(float(y))
        nodeYList.append(float(z))
        #f"({x},{y})")
    count += 1

def NormalizeData(data):
    return (data - np.min(data)) / (np.max(data) - np.min(data))

xNorm = NormalizeData(x)
print(xNorm)

colors = [(r, 0, 1-r) for r in xNorm]

# ScatterPlot of the nodes
plt.ioff()
plt.figure(figsize=(100,100), dpi=100)
plt.scatter(nodeXList, nodeYList, s=400, c=colors)
plt.title("Manhatan")
plt.savefig("Manhatan3.png", dpi=100, transparent=True)

[4.44431787 3.59237952 4.12763834 ... 4.68405992 5.61035138 4.09557523]
Graph with 8708 nodes and 13556 edges
[0.42854766 0.32505918 0.39007929 ... 0.45767012 0.57019058 0.38618445]


## Conclusão

Nesse sentido, é possível concluir que a resolução do sistema linear encontrado através da representação da matriz cheia nos métodos listados chega em uma solução satisfatória. Entretanto, os métodos iterativos gastam demasiado tempo de execução, o que representa um impasse para sistemas com componentes na ordem de milhões, que poderiam demorar meses para serem resolvidos, além de ter a possibilidade de que a memória necessária não pudesse ser atendida pelos computadores pessoais atuais. Desse modo, é observável que a utilização da representação em matriz esparsa tem uma melhora significativa de performance para a resolução do sistema linear, apresentando uma diferença gritante em tempo de execução.